#MVP Engenharia de Dados - 2025
Thomas A. S. Abrantes


### Setup para rodar o notebook com os dados
- Imports das bibliotecas para consumo dos dados.

In [0]:
#bibioteca para uso do comando com Pandas
import pandas as pd

#biblioteca para carga de dados e request dos dados
import io
import requests

#Criando Banco de Dados (schema) com os Relatórios (Visões)


In [0]:
%sql
-- Removendo Schema para recriar
DROP SCHEMA IF EXISTS IMDB_RELATORIO CASCADE;

-- CRIANDO O BANCO DE DADOS (schema)
CREATE SCHEMA IMDB_RELATORIO;

#Relatórios

Neste notebook podemos consultar a criação das visões (consultas) utilizando como fonte a base (IMDB_DB_GOLD) **Camada GOLD** de forma a responder a cada uma das perguntas.

###Quantidade de títulos lançados no Brasil por categoria e década (80, 90, etc.).

In [0]:
%sql
CREATE OR REPLACE VIEW IMDB_RELATORIO.VW_LANCAMENTO_POR_TIPO_DECADA
AS
  SELECT
    CASE WHEN DECADA > 0 THEN concat('19', DECADA,'0') ELSE concat('20', DECADA,'0') END DECADA,
    CATEGORIA,
    QUANTIDADE TITULOS_LANCADOS
  FROM (
    SELECT 
      CATEGORIA, COUNT(0) QUANTIDADE, substring(ANO_LANCAMENTO, 2, 1) DECADA
    FROM imdb_db_gold.tb_filme_lancamento_brasil
    GROUP BY CATEGORIA, substring(ANO_LANCAMENTO, 2, 1)
  ) CONSULTA
  ORDER BY decada, TITULOS_LANCADOS DESC, CATEGORIA
  ;

  -- EXIBINDO RESULTADO
SELECT * FROM IMDB_RELATORIO.VW_LANCAMENTO_POR_TIPO_DECADA;

DECADA CATEGORIA TITULOS_LANCADOS 1980 short 76 1990 movie 41553 1990 short 5383 1990 video 1127 2000 movie 31863 2000 short 12476 2000 video 4212

Databricks visualization. Run in Databricks to view.

###Qual categoria teve mais lançamentos no Brasil por década?

In [0]:
%sql
CREATE OR REPLACE VIEW IMDB_RELATORIO.VW_CATEGORIAS_COM_MAIS_LANCAMENTO_BRASIL
AS
SELECT
  VISAO_GERAL.DECADA,
  CASE VISAO_GERAL.CATEGORIA
    WHEN 'movie' THEN 'Filme'
    WHEN 'video' THEN 'Vídeo (dvd, vhs, etc.)'
    WHEN 'short' THEN 'Curta metralgem'
  ELSE VISAO_GERAL.CATEGORIA end CATEGORIA_MAIOR_QUANTIDADE_LANCAMENTOS,
  LANCAMENTOS.TITULOS_LANCADOS QUANTIDADE
FROM 
  IMDB_RELATORIO.VW_LANCAMENTO_POR_TIPO_DECADA VISAO_GERAL,
  (
    SELECT DECADA, MAX(TITULOS_LANCADOS) TITULOS_LANCADOS 
    FROM IMDB_RELATORIO.VW_LANCAMENTO_POR_TIPO_DECADA
    GROUP BY DECADA
  ) LANCAMENTOS
WHERE VISAO_GERAL.DECADA = LANCAMENTOS.DECADA AND VISAO_GERAL.TITULOS_LANCADOS = LANCAMENTOS.TITULOS_LANCADOS
ORDER BY VISAO_GERAL.DECADA
;

-- EXIBINDO RESULTADO
SELECT * FROM IMDB_RELATORIO.VW_CATEGORIAS_COM_MAIS_LANCAMENTO_BRASIL;

DECADA CATEGORIA_MAIOR_QUANTIDADE_LANCAMENTOS QUANTIDADE 1980 Curta metralgem 76 1990 Filme 41553 2000 Filme 31863

Databricks visualization. Run in Databricks to view.

###Todos os títulos que possuem nome exclusivo no Brasil (Com nome diferente do nome original ou comercial).

- **Conforme análise** na criação da tabela **IMDB_DB_BRONZE.tb_title_akas**, identificamos que não há título com campo isOriginalTitle  = 1 (True) com o campo region preenchido. 
- Mesmo que o titulo TITULO_ORIGINAL seja igual o TITULO de lançamento e descrito em português, não podemos afirmar que seja um Título produzido no Brasil, devido a falta da informação de ser um título Original. 
- Desta forma todos os titulos duplicados que tenha a coluna IDIOMA com valor "pt" e outra com valor nulo (NULL) e analisando as informações fornecidas pelo Dicionário de Dados; concluo que o registro do título com campo IDIOMA preenchido é um título legendado ou dublado.

In [0]:
%sql
CREATE OR REPLACE VIEW IMDB_RELATORIO.VW_TITULOS_COM_NOME_EXCLUSIVO_NO_BRASIL
AS
SELECT 
  TITULO TITULO_BRASIL,
  TITULO_ORIGINAL TITULO_ORIGINAL,
  TITULO_PRIMARIO TITULO_COMERCIAL,
  ANO_LANCAMENTO
FROM 
  IMDB_DB_GOLD.tb_filme_lancamento_brasil
WHERE
  TRIM(TITULO) <> TRIM(TITULO_ORIGINAL) OR TRIM(TITULO) <> TRIM(TITULO_PRIMARIO)
GROUP BY
  TITULO_PRIMARIO, 
  TITULO_ORIGINAL, 
  TITULO, 
  ANO_LANCAMENTO
ORDER BY TITULO
;

-- EXIBINDO RESULTADO
SELECT * FROM IMDB_RELATORIO.VW_TITULOS_COM_NOME_EXCLUSIVO_NO_BRASIL;

TITULO_BRASIL TITULO_ORIGINAL TITULO_COMERCIAL ANO_LANCAMENTO #ALIVE #SARAITDA #ALIVE 2020 #ERADOSGIGANTES #ERADOSGIGANTES #ONTHESHOULDERSOFGIANTS 2020 #GAROTAS: O FILME #GAROTAS: O FILME #THOSEGIRLS 2015 #MANHOLE - DESVIO FATAL #MANHOLE #MANHOLE 2023 #OITAVO OITAVO OITAVO 2017 #PARTIUFAMA: CANCELADO NO AMOR #PARTIUFAMA: CANCELADO NO AMOR #FAMETIME 2022 #RESISTÊNCIA #RESISTÊNCIA #RESISTANCE 2017 #SEMFILTRO #NOFILTER #NOFILTER 2013 #SEMSAÍDA #FOLLOWME #FOLLOWME 2019 #SEMSAÍDA FOLLOW ME FOLLOW ME 2020 #SEM_FILTRO - NOITE SANGRENTA #NO_FILTER #NO_FILTER 2022 #SOBREVIVA #SARAITDA #ALIVE 2020 #UBERXTAXIS #UBERXTAXIS UBER VS. TAXI 2022 'BENNY: MEU FILHOTE FAVORITO' UGLY BENNY UGLY BENNY 2014 'DESPEDIDA DE FORMANDOS/SEMANA DO BARULHO' SENIOR WEEK SENIOR WEEK 1988 'ELA' CURTAS EXTRAS: O AMOR NA IDADE MODERNO HER: LOVE IN THE MODERN AGE HER: LOVE IN THE MODERN AGE 2014 'ELA' CURTAS EXTRAS: O PROJETO SEM NOME DE RICK HOWARD HER: THE UNTITLED RICK HOWARD PROJECT HER: THE UNTITLED RICK HOWARD PROJECT 2014 'ELES' SE DIVERTEM THE GAY DECEIVERS THE GAY DECEIVERS 1969 'MENINO SATÉLITE' SATELLITE BOY SATELLITE BOY 2012 'OS REIS DO FLEXING' FLEX IS KINGS FLEX IS KINGS 2013 'SEXTA-FEIRA' MAN FRIDAY MAN FRIDAY 1975 (500) DIAS COM ELA (500) DAYS OF SUMMER 500 DAYS OF SUMMER 2009 (A) FRONTEIRA FRONTIÈRE(S) FRONTIER(S) 2007 (DES)ENCONTRO PERFEITO MAN UP MAN UP 2015 (IN) SEGUROS BAD IMPULSE BAD IMPULSE 2019 (R)EVOLUÇÃO DA CARNE STEAK (R)EVOLUTION STEAK (R)EVOLUTION 2014 (RE)NASCER BIRTH/REBIRTH BIRTH/REBIRTH 2023 + VELOZES + FURIOSOS 2 FAST 2 FURIOUS 2 FAST 2 FURIOUS 2003 ...DE QUE LADO ESTÁS/ FRANCISCA FRANCISCA 2002 ...DE QUE LADO ESTÁS? FRANCISCA FRANCISCA 2002 ...E AGORA ME CHAMAM 'O MAGNÍFICO' E POI LO CHIAMARONO IL MAGNIFICO MAN OF THE EAST 1972 ...E AS RUIVAS CHEGARAM THOSE REDHEADS FROM SEATTLE THOSE REDHEADS FROM SEATTLE 1953 ...E CHAMARAM GRINGO PARA MATAR LA NOTTE DEI SERPENTI NIGHT OF THE SERPENT 1969 ...E DEUS OUVIU SUAS PRECES UN TRAJE BLANCO MIRACLE OF THE WHITE SUIT 1956 ...E DOS INIMIGOS ME LIVRO EU DAI NEMICI MI GUARDO IO! I PROTECT MYSELF AGAINST MY ENEMIES 1968 ...E FRANKENSTEIN CRIOU A MULHER FRANKENSTEIN CREATED WOMAN FRANKENSTEIN CREATED WOMAN 1967 ...E NISTO CHEGOU A MULHER THEN CAME THE WOMAN THEN CAME THE WOMAN 1926 ...E O AMOR VOLTOU TOGETHER AGAIN TOGETHER AGAIN 1944 ...E O BRAVO FICOU SÓ WILL PENNY WILL PENNY 1967 ...E O DEMÔNIO CRIOU OS HOMENS ...Y EL DEMONIO CREÓ A LOS HOMBRES HEAT 1960 ...E O ESPETÁCULO É FABULOSO TRAUMREVUE DREAM REVUE 1959 ...E O MUNDO SE DIVERTE E O MUNDO SE DIVERTE E O MUNDO SE DIVERTE 1948 ...E O NOIVO VOLTOU NO ROOM FOR THE GROOM NO ROOM FOR THE GROOM 1952 ...E O VENTO LEVOU GONE WITH THE WIND GONE WITH THE WIND 1939 ...E OS ANOS PASSARAM MOTHER WORE TIGHTS MOTHER WORE TIGHTS 1947 ...E TUDO INDICA BERLIM DIE SPUR FÜHRT NACH BERLIN ADVENTURE IN BERLIN 1952 ...E UM CADÁVER NÃO VOLTOU THE MISSING CORPSE THE MISSING CORPSE 1945 ...LEQUE DE PAVÃO THE PEACOCK FAN THE PEACOCK FAN 1929 ...UM TERÇO DE UMA NAÇÃO... ...ONE THIRD OF A NATION... ...ONE THIRD OF A NATION... 1939 .45 - A VITÓRIA É A VINGANÇA .45 .45 2006 .COM PARA MORRER (NET GAMES) NET GAMES NET GAMES 2003 00 KID, UM ESPIÃO MUITO ESPECIAL THE DOUBLE 0 KID THE DOUBLE 0 KID 1992 00-2 - LOUCOS DE PARAQUEDAS I DUE PARÀ I DUE PARÀ 1965 00-2 MAFIOSOS CONTRA GOLDGINGER DUE MAFIOSI CONTRO GOLDGINGER THE AMAZING DOCTOR G 1965 00-DOIS AGENTES SECRETÍSSIMOS 002 AGENTI SEGRETISSIMI OH! THOSE MOST SECRET AGENTS 1964 00-DOIS FUGITIVOS DE SING-SING I DUE EVASI DI SING SING I DUE EVASI DI SING SING 1964 002: PERIGOS PÚBLICOS I DUE PERICOLI PUBBLICI I DUE PERICOLI PUBBLICI 1964 007 - A SERVIÇO SECRETO DE SUA MAJESTADE ON HER MAJESTY'S SECRET SERVICE ON HER MAJESTY'S SECRET SERVICE 1969 007 - AO SERVIÇO DE SUA MAJESTADE ON HER MAJESTY'S SECRET SERVICE ON HER MAJESTY'S SECRET SERVICE 1969 007 - CASSINO ROYALE CASINO ROYALE CASINO ROYALE 2006 007 - MARCADO PARA A MORTE THE LIVING DAYLIGHTS THE LIVING DAYLIGHTS 1987 007 - MARCADO PARA MORRER THE LIVING DAYLIGHTS T

###Qual a porcentagem de pessoas que atuaram como Ator ou Atriz em Títulos do tipo Filmes, Curtas ou Vídeo, lançados no Brasil?

- Pela profissão da pessoa será definido seu sexo como Masculino (actor) ou Feminino (actress)

In [0]:
%sql
CREATE OR REPLACE VIEW IMDB_RELATORIO.VW_PORCENTAGEM_SEXO_EM_TITULOS_NO_BRASIL
AS
SELECT 
  TOTAL.TODOS,
  SEXO_FEMININO.TOTAL FEMININO,
  SEXO_MASCULINO.TOTAL MASCULINO,
  decimal(SEXO_FEMININO.TOTAL * 100 / TOTAL.TODOS) PORCENTAGEM_FEMININO,
  decimal(SEXO_MASCULINO.TOTAL * 100 / TOTAL.TODOS) PORCENTAGEM_MASCULINO
FROM
  (SELECT COUNT(0) AS TODOS
    FROM IMDB_DB_GOLD.TB_ATOR_TITULO 
    WHERE PROFISSAO1 = 'actor' OR PROFISSAO1 = 'actress' OR PROFISSAO2 = 'actor' OR PROFISSAO2 = 'actress' OR PROFISSAO3 = 'actor' OR PROFISSAO3 ='actress') TOTAL,
  (SELECT COUNT(0)  AS TOTAL FROM IMDB_DB_GOLD.TB_ATOR_TITULO WHERE PROFISSAO1 = 'actress' OR PROFISSAO2 = 'actress' OR PROFISSAO3 = 'actress') SEXO_FEMININO,
  (SELECT COUNT(0) AS TOTAL FROM IMDB_DB_GOLD.TB_ATOR_TITULO WHERE PROFISSAO1 = 'actor' OR PROFISSAO2 = 'actor' OR PROFISSAO3 = 'actor') SEXO_MASCULINO
;

SELECT * FROM IMDB_RELATORIO.VW_PORCENTAGEM_SEXO_EM_TITULOS_NO_BRASIL;

TODOS FEMININO MASCULINO PORCENTAGEM_FEMININO PORCENTAGEM_MASCULINO 895200 276415 618854 31 69

Databricks visualization. Run in Databricks to view.

##Porcentagem de atores do sexo feminino e masculino que atuaram nos títulos do tipo Filme em cada década existente na base.
- Para o resultado, criação da View IMDB_RELATORIO.VW_TOTAL_POR_DECADA_GENERO_ATOR que vai estruturar a consulta para o cálculo das porcentagens.
- Obter a porcentagem de atores do sexo feminino e masculino que atuaram nos títulos do tipo Filme em cada década existente na base.

In [0]:
%sql
-- Criando visão geral para o relatório
CREATE OR REPLACE VIEW IMDB_RELATORIO.VW_TOTAL_POR_DECADA_SEXO_ATOR
AS
SELECT 
  SEXO,
  DECADA,
  TOTAL
FROM
  (
    SELECT
      CASE 
        WHEN ATOR_TITULO.SEXO = 'M' THEN 'MASCULINO'
        WHEN ATOR_TITULO.SEXO = 'F' THEN 'FEMININO'
      ELSE 'NÃO INFORMADO'
      END SEXO,
      CASE WHEN substring(FILMES.ANO_LANCAMENTO, 2, 1) > 0 
        THEN concat('19', substring(FILMES.ANO_LANCAMENTO, 2, 1),'0') 
        ELSE concat('20', substring(FILMES.ANO_LANCAMENTO, 2, 1),'0') 
      END DECADA,
      count(0) TOTAL
    FROM
      IMDB_DB_GOLD.TB_ATOR_TITULO_BRASIL AS ATOR_TITULO,
      IMDB_DB_GOLD.TB_FILME_LANCAMENTO_BRASIL FILMES
    WHERE FILMES.CHAVE_TITULO = ATOR_TITULO.CHAVE_TITULO
    GROUP BY 
      ATOR_TITULO.SEXO,  
      substring(FILMES.ANO_LANCAMENTO, 2, 1)
    ORDER BY DECADA
  ) AS CONSULTA;

  SELECT * FROM IMDB_RELATORIO.VW_TOTAL_POR_DECADA_SEXO_ATOR;

SEXO DECADA TOTAL NÃO INFORMADO 1980 3 FEMININO 1980 26 MASCULINO 1980 70 NÃO INFORMADO 1990 1692463 FEMININO 1990 859893 MASCULINO 1990 2560843 NÃO INFORMADO 2000 1198201 FEMININO 2000 448839 MASCULINO 2000 937719

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
-- Criando consulta
SELECT 
  TODOS.TOTAL,
  decimal(FEMININO.TOTAL*100 / TODOS.TOTAL) PORCENTAGEM_FEMININO,
  decimal(MASCULINO.TOTAL*100 / TODOS.TOTAL) PORCENTAGEM_MASCULINO,
  decimal(NAO_INFORMADO.TOTAL*100 / TODOS.TOTAL) PORCENTAGEM_NAO_INFORMADO,
  TODOS.DECADA
FROM
  (SELECT SUM(TOTAL) TOTAL, DECADA FROM IMDB_RELATORIO.VW_TOTAL_POR_DECADA_SEXO_ATOR GROUP BY DECADA) AS TODOS,
  (SELECT TOTAL, DECADA FROM IMDB_RELATORIO.VW_TOTAL_POR_DECADA_SEXO_ATOR WHERE SEXO = 'MASCULINO') AS MASCULINO,
  (SELECT TOTAL, DECADA FROM IMDB_RELATORIO.VW_TOTAL_POR_DECADA_SEXO_ATOR WHERE SEXO = 'FEMININO') AS FEMININO,
  (SELECT TOTAL, DECADA FROM IMDB_RELATORIO.VW_TOTAL_POR_DECADA_SEXO_ATOR WHERE SEXO = 'NÃO INFORMADO') AS NAO_INFORMADO
WHERE 
  TODOS.DECADA = FEMININO.DECADA
  AND FEMININO.DECADA = MASCULINO.DECADA
  AND MASCULINO.DECADA = NAO_INFORMADO.DECADA
ORDER BY TODOS.DECADA
;

TOTAL PORCENTAGEM_FEMININO PORCENTAGEM_MASCULINO PORCENTAGEM_NAO_INFORMADO DECADA 99 26 71 3 1980 5113199 17 50 33 1990 2584759 17 36 46 2000

###Filmes lançados no Brasil, onde o Diretor(a) atuou como Ator/Atriz.

In [0]:
%sql
SELECT 
  ATOR_TITULO.NOME_ARTISTICO,
  FILME.TITULO_ORIGINAL,
  FILME.ANO_LANCAMENTO,
  FILME.REGIAO,
  ATOR_TITULO.PROFISSAO1,
  ATOR_TITULO.PROFISSAO2,
  ATOR_TITULO.PROFISSAO3
FROM 
  IMDB_DB_GOLD.TB_ATOR_TITULO AS ATOR_TITULO,
  IMDB_DB_GOLD.TB_FILME_LANCAMENTO_BRASIL AS FILME
WHERE 
  ATOR_TITULO.DIRETOR_TITULO = 'S'
  AND (ATOR_TITULO.PROFISSAO1 LIKE 'act%' OR ATOR_TITULO.PROFISSAO2 LIKE 'act%' OR ATOR_TITULO.PROFISSAO3 LIKE 'act%')
  AND (
    FILME.CHAVE_TITULO = ATOR_TITULO.TCONST1 
    OR FILME.CHAVE_TITULO = ATOR_TITULO.TCONST2 
    OR FILME.CHAVE_TITULO = ATOR_TITULO.TCONST3 
    OR FILME.CHAVE_TITULO = ATOR_TITULO.TCONST4
  )  
GROUP BY 
  ATOR_TITULO.NOME_ARTISTICO,
  FILME.TITULO_ORIGINAL,
  FILME.ANO_LANCAMENTO,
  FILME.REGIAO,
  ATOR_TITULO.PROFISSAO1,
  ATOR_TITULO.PROFISSAO2,
  ATOR_TITULO.PROFISSAO3
ORDER BY ATOR_TITULO.NOME_ARTISTICO, FILME.TITULO_ORIGINAL
;


NOME_ARTISTICO TITULO_ORIGINAL ANO_LANCAMENTO REGIAO PROFISSAO1 PROFISSAO2 PROFISSAO3 'Philthy' Phil Phillips CITY DRAGON 1995 BR director actor writer A. Edward Sutherland ABIE'S IRISH ROSE 1946 BR director producer actor A. Edward Sutherland SKY DEVILS 1932 BR director producer actor A. Edward Sutherland STEEL AGAINST THE SKY 1941 BR director producer actor A. Edward Sutherland THE SAP FROM SYRACUSE 1930 BR director producer actor A.R. Murugadoss GHAJINI 2008 BR writer director actor AJ Jones THE CURSE OF LA PATASOLA 2022 BR actor writer director Aage Rais-Nordentoft 2 RYK OG EN AFLEVERING 2003 BR director writer actor Aakash Bhatia LOOOP LAPETA 2022 BR director writer actor Aarne Tarkas NINA JA ERIK 1960 BR director writer actor Aaron Bertrand-Ruiz ERÓTICO 2024 BR director actor writer Aaron Fisher INSIDE THE RAIN 2019 BR actor director writer Aaron Harnick 30 DAYS 1999 BR actor writer producer Aaron Harnick JUDY BERLIN 1999 BR actor writer producer Aaron Sorkin A FEW GOOD MEN 1992 BR writer producer actor Aaron Sorkin MOLLY'S GAME 2017 BR writer producer actor Aaron Sorkin THE TRIAL OF THE CHICAGO 7 2020 BR writer producer actor Abdellatif Kechiche L'ESQUIVE 2003 BR writer director actor Abdellatif Kechiche LA FAUTE À VOLTAIRE 2000 BR writer director actor Abdellatif Kechiche LA GRAINE ET LE MULET 2007 BR writer director actor Abdellatif Kechiche LA VIE D'ADÈLE 2013 BR writer director actor Abel Ferrara BAD LIEUTENANT 1992 BR director actor writer Abel Ferrara KING OF NEW YORK 1990 BR director actor writer Abel Ferrara NEW ROSE HOTEL 1998 BR director actor writer Abel Ferrara ZEROS AND ONES 2021 BR director actor writer Abel Salazar EL BARÓN DEL TERROR 1962 BR actor producer director Abhilash Shetty KOLI TAAL 2021 BR director writer actor Abhinav Kashyap DABANGG 2010 BR director writer actor Abhinay Deo BLACKMAIL 2018 BR director producer actor Abhinay Deo DELHI BELLY 2011 BR director producer actor Abhinay Deo SAVI 2024 BR director producer actor Abhishek Kapoor CHANDIGARH KARE AASHIQUI 2021 BR director writer actor Abilio Pereira de Almeida DONA VIOLANTE MIRANDA 1960 BR writer producer actor Abilio Pereira de Almeida NADANDO EM DINHEIRO 1952 BR writer producer actor Abilio Pereira de Almeida SAI DA FRENTE 1952 BR writer producer actor Abilio Pereira de Almeida ÂNGELA 1951 BR writer producer actor Abner Biberman GUNGA DIN 1939 BR director actor writer Abner Biberman HIS GIRL FRIDAY 1940 BR director actor writer Abner Biberman WINCHESTER '73 1950 BR director actor writer Abram Room TRETYA MESHCHANSKAYA 1927 BR director writer actor Achero Mañas NOVIEMBRE 2003 BR actor director writer Achmed Abdel-Salam HEIMSUCHUNG 2023 BR actor producer director Adam Alleca CELL 2016 BR writer director actor Adam Alleca DELIRIUM 2018 BR writer director actor Adam Alleca STANDOFF 2016 BR writer director actor Adam Alleca THE LAST HOUSE ON THE LEFT 2009 BR writer director actor Adam Christian Clark DIARY OF A SPY 2022 BR director writer actor Adam Coleman Howard DARK HARBOR 1998 BR actor director writer Adam Coleman Howard DEAD GIRL 1996 BR actor director writer Adam Collis SUNSET STRIP 2000 BR director producer actor Adam Gierasch TOOLBOX MURDERS 2004 BR actor writer director Adam Goldberg A BEAUTIFUL MIND 2001 BR actor writer director Adam Goldberg DAZED AND CONFUSED 1993 BR actor writer director Adam Goldberg DEJA VU 2006 BR actor writer director Adam Goldberg SAVING PRIVATE RYAN 1998 BR actor writer director Adam Green FROZEN 2010 BR director writer actor Adam Green HATCHET 2006 BR director writer actor Adam Green JUNO 2007 BR actor director producer Adam Green PLAYING IT COOL 2014 BR actor director producer Adam Green WHIP IT 2009 BR actor director producer Adam Hobzik UBAL A ZMIZ 2021 BR director actor writer Adam Leon TRAMPS 2016 BR director writer actor Adam MacDonald BACKCOUNTRY 2014 BR actor director writer Adam MacDonald PYEWACKET 2017 BR actor director writer Adam MacDonald THANKSGIVING 2023 BR actor director writer Adam Marcus J

##Ranking dos diretores com títulos lançados no Brasil.
- Diretores com maior numero de participação na direção de títulos lançados no Brasil.

In [0]:
%sql
SELECT
  NOME_ARTISTICO,
  count(CHAVE_TITULO) TOTAL
FROM 
(
  SELECT
    ATOR_TITULO.NOME_ARTISTICO,
    ATOR_TITULO.CHAVE_TITULO
  FROM 
    IMDB_DB_GOLD.TB_ATOR_TITULO_BRASIL AS ATOR_TITULO,
    IMDB_DB_GOLD.TB_FILME_LANCAMENTO_BRASIL AS FILME
  WHERE 
    ATOR_TITULO.DIRETOR_TITULO = 'S'
    AND TRIM(FILME.CHAVE_TITULO) = TRIM(ATOR_TITULO.CHAVE_TITULO)
  GROUP BY ATOR_TITULO.NOME_ARTISTICO,
    ATOR_TITULO.CHAVE_TITULO
) AS DIRETOR_TITULOS
GROUP BY NOME_ARTISTICO
ORDER BY count(CHAVE_TITULO) DESC
;

NOME_ARTISTICO TOTAL Pedro Murad 9 John Waters 8 Luciano Mello 8 Bruno de Oliveira 8 Bruno Costa 8 Marcelo Leme 8 Leonardo Martinelli 8 Anna Azevedo 7 George Miller 7 Joaquim Haickel 7 Maria Ribeiro 7 Paulo Miranda 7 Robert Gordon 7 Christian Caselli 7 Carlos Pronzato 6 Bruno Mello 6 Pedro Tavares 6 Simon Wells 6 Letícia Simões 6 Alex Reis 6 Tim Sullivan 6 Michael Mayer 6 Eduardo Mattos 6 Amir Admoni 6 Diego Lima 6 Marcelo Santiago 5 José Carlos Lage 5 Paulo Nascimento 5 Gustavo Ribeiro 5 Athanasios Kalogiannis 5 Emílio Domingos 5 Pablo Ferreira 5 Adam Green 5 Paulo Ernesto 5 Paul Levine 5 Richard Greenberg 5 André Luiz Oliveira 5 Hugo Moura 5 Washington Carvalho 5 John Hoffman 5 Claudia Nunes 5 Danny Lerner 5 David Douglas 5 Alison Zago 5 Kim Ki-duk 5 Ricardo Miranda 5 Daniel Aragão 5 Guilherme Jardim 5 Tommy Chong 4 Donato Viero 4 Michael Gordon 4 Leonardo Fiorito 4 Mia Marzy 4 Diego Locatelli 4 Amanda Doria 4 Joy Chapman 4 Laurence Olivier 4 Phil Dornfeld 4 Will Gluck 4 Jim Jarmusch 4 Clodoaldo Lino 4 Dave Kim 4 Karen Leigh Hopkins 4 Wash Westmoreland 4 Eduardo Hirtz 4 Wayne Kramer 4 L.H. Girarde 4 Nicholas Meyer 4 Sam Upton 4 Priscilla Brasil 4 James Sbardellati 4 Paulo Leão 4 Jûzô Itami 4 Christopher Neil 4 Sabrina Trentim 4 Rob Schneider 4 Marcela Moura 4 Michel Qissi 4 Sung Sfai 4 Daniela Thomas 4 Sheldon Lettich 4 Vinicius Nascimento 4 Thomas Napper 4 John Rawlins 4 Alexis Müller 4 Daniel Turini 4 Antônio F. Souza Filho 4 Claude Berri 4 Josh C. Waller 4 Rainer Werner Fassbinder 4 Ugo Lombardi 4 Jonathan del Val 4 Tom Ford 4 Barry Cook 4 João Victor Borges 4 Jefferson Assunção 4 Ryoo Seung-wan 4 George Tillman Jr. 4 Stan Haze 4 Rita Carelli 4 Roberto Hades 4 Pedro Miyoshi 4 Mike Gunther 4 Mitchell Lichtenstein 4 Genil Vasconcelos 4 Stanton Barrett 4 Beto Perocini 4 Robert Legato 4 Steven Seagal 4 Madonna 4 Julie Delpy 4 Hun Jang 4 Stuart Beattie 4 Sergio Amon 4 Conrad Nagel 4 Tim Roth 4 Mojgan Khadem 4 Richard Pryor 4 Tizuka Yamasaki 4 Silvio Tendler 4 Ted Wilde 4 Isa Meneghini 4 Maggie Gyllenhaal 4 Lucílio Jota 4 Anna Israel 4 Samuel Lobo 4 Hongsun Kim 4 Samira Makhmalbaf 4 Joseph Anthony 4 Kim Dae-woo 4 Paulo Leite Soares 4 Ricardo Araripe 4 Jacob Johnston 4 Eugene Forde 4 Isac Domingos 4 Eric Tsang 4 Griffin Dunne 4 Bentinho 4 Mark Waters 4 Benoît Jacquot 4 Júpiter Maçã 4 Raul Roulien 4 Stuart Townsend 4 Jim Clark 4 Yvan Attal 4 Edivaldo Moura 4 Leonardo Brant 4 J. Christian Ingvordsen 4 David Butler 4 Roney Freitas 4 Joseph A. McDonough 4 Jim Cummings 4 Saul Lachtermacher 4 Ti West 4 Cesar Coffin Souza 4 Christopher McQuarrie 4 Danny DeVito 4 Fernando Bassani 4 Gabriel Figueira 4 Denzel Washington 4 Reem Kherici 4 Akira Kurosawa 4 Mauricio Lidio 4 Otho Lovering 4 Tay Garnett 4 Mozart Cintra 4 Leo Tabosa 4 Cecílio Neto 4 Mira Nair 4 Richard Fleischer 4 Billy Bob Thornton 4 Emilia Silveira 4 Denise Dowse 4 Giordano Gio 4 Kôzô Kusuba 4 Herbert Bianchi 4 Magnum Borges Borini 4 Angelo Lima 4 Jérôme Salle 4 Chad Burns 4 Rich Cowan 4 Franklin A. Vallette 4 Marcelo Fabri Marão 4 Johann Jean 4 Raoul Lévy 4 Marcelo Taranto 4 Cláudio Cunha 4 Jean Grimard Gauthereau 4 Pedro Amorim 4 F. Hugh Herbert 4 Felipe Poroger 4 Frank Marshall 4 Jim Sheridan 4 Jimmy Sangster 4 Raymond Martino 4 Terrence Malick 4 Denise Vieira 4 Carla Camurati 4 Jorge Mendes 4 Filipi Nunes 4 Gustavo Menezes 4 Roque Araújo 4 Pedro Monte Kling 4 Danny Leiner 4 Sanin Cherques 4 Sydney Pollack 4 Silvio Da-Rin 4 Jean Genet 4 Zoran Djordjevic 4 Louis Leterrier 4 Keiichi Hara 4 Roberto Filho 4 Maximilian Schell 4 Rafael Van Hayden 4 Andrea Fergo 4 Kevin Johnson 4 Reginaldo Faria 4 Rowdy Herrington 4 Hugo Carvana 4 Jordan Peele 4 Calebe Lopes 4 Alan Parker 4 René Goscinny 4 P.J. Wolfson 4 Fernanda Teixeira 4 Daniel Taradash 4 Saskia Sá 4 Enrico Casarosa 4 Frederico Machado 4 William Teitler 4 Douglas Day Stewart 4 Tila Chitunda 4 Rob Cohen 4 Roberto Machado 4 Vandré Fernandes 4 Daniel Petrie Jr. 4 Rafael Montelori Castro 4 Peter Weir 4 André Pacheco 4 Edgard Cavalc